In [1]:
import plotly.express as px
import allel
import numpy as np
import pandas as pd

def sample_diversity(geno, samples, pos):
    pis = []
    for i, sample in enumerate(samples):
        ac = geno.take([i], axis=1).count_alleles()
        pis.append(allel.sequence_diversity(ac=ac, pos=np.arange(len(pos))))

    return pd.DataFrame({'sample_id':samples, 'pi':pis})

def cohort_diversity(geno, pos, samples, metadata, cohort_col):
    cohs = metadata[cohort_col].unique()
    cohs = cohs[~pd.isnull(cohs)] #remove nan cohorts
    coh_idxs = {loc:np.where(metadata[cohort_col] == loc)[0] for loc in cohs}

    pis = []
    for coh in cohs:
        ac = geno.take(coh_idxs[coh], axis=1).count_alleles()
        pis.append(allel.sequence_diversity(ac=ac, pos=np.arange(len(pos))))   

    return pd.DataFrame({'cohort':cohs, 'pi':pis}) 

In [2]:
dataset = 'vigg-01'
metadata_path = "../../results/config/metadata.qcpass.tsv"
cohort_cols = 'location,taxon'
vcf_path = "../../results/vcfs/amplicons/ampseq-vigg-01.annot.vcf"
wkdir = "../.."

In [3]:
# Parameters
dataset = "ag-vampir-002"
vcf_path = "results/vcfs/amplicons/ag-vampir-002.annot.vcf"
wkdir = "/home/snagi/lstm_projects/ampseq-agvampir002"
cohort_cols = "location,taxon"
metadata_path = "results/config/metadata.qcpass.tsv"


In [4]:
import sys
import os
sys.path.append(os.path.join(wkdir, 'workflow'))
import ampseekertools as amp

### Genetic diversity

This page calculates genetic diversity in individuals and cohorts. 

*Note*: Calculating genetic diversity from ag-vampir amplicons is tricky because there are so many Vgsc / IR amplicons, results will be biased by the presence of selective sweeps, and aims. 

In [5]:
cohort_cols = cohort_cols.split(",")

# load metadata
if metadata_path.endswith('.xlsx'):
    metadata = pd.read_excel(metadata_path, engine='openpyxl')
elif metadata_path.endswith('.tsv'):
    metadata = pd.read_csv(metadata_path, sep="\t")
elif metadata_path.endswith('.csv'):
    metadata = pd.read_csv(metadata_path, sep=",")
else:
    raise ValueError("Metadata file must be .xlsx or .csv")

geno, pos, contig, metadata, ref, alt, ann = amp.load_vcf(vcf_path, metadata)
samples = metadata['sample_id'].values

/home/snagi/lstm_projects/ampseq-agvampir002/.snakemake/conda/f966e7e3ce97283061977315ab7eb56b_/lib/python3.12/site-packages/allel/io/vcf_read.py:1732: UserWarning: invalid INFO header: '##INFO=<ID=VDB,Number=1,Type=Float,Description="Variant Distance Bias for filtering splice-site artefacts in RNA-seq data (bigger is better)",Version="3">\n'
  warnings.warn('invalid INFO header: %r' % header)


#### By cohort

In [6]:
for coh in cohort_cols:
    df_cohort_pi = cohort_diversity(
        geno=geno, 
        pos=pos,
        samples=samples, 
        metadata=metadata, 
        cohort_col=coh
    )
    df_cohort_pi.to_csv(f"{wkdir}/results/genetic-diversity/{coh}.pi.tsv", sep="\t")
    
    fig = px.bar(df_cohort_pi, x='cohort', y='pi', template='simple_white', width=600, height=400)
    fig.show()

In [7]:
sample_pi_df = sample_diversity(geno=geno, samples=samples, pos=pos)
sample_pi_df.to_csv(f"{wkdir}/results/genetic-diversity/samples.pi.tsv", sep="\t")